In [1]:
import numpy as np
import pandas as pd
import datetime

DATA_PATH = 'files/'

df = pd.read_csv(DATA_PATH + 'covid_train_country_june_22.csv')\
        [['date', 'key', 'confirmed', 'deaths', 'recovered', 'confirmed_new', 'active']]
df['date'] = df['date'].apply(lambda x: (datetime.datetime.strptime(x, '%m/%d/%y')))
df['days'] = (df['date'].dt.date - df['date'].dt.date.min()).dt.days

population = pd.read_csv(DATA_PATH + 'backtesting/Population.csv')

print(df.shape)
df.head()


(38709, 8)


date          key  confirmed  deaths  recovered  confirmed_new  \
0 2020-01-22  Afghanistan          0       0          0            0.0   
1 2020-01-23  Afghanistan          0       0          0            0.0   
2 2020-01-24  Afghanistan          0       0          0            0.0   
3 2020-01-25  Afghanistan          0       0          0            0.0   
4 2020-01-26  Afghanistan          0       0          0            0.0   

   active  days  
0       0     0  
1       0     1  
2       0     2  
3       0     3  
4       0     4

In [2]:
SAVE_PATH = "figs"

In [3]:
from sklearn.metrics import mean_squared_error

def loss_mae(ytrue, pred):
    "MAE"
    assert ytrue.shape == pred.shape
    return np.mean(np.abs(pred.flatten()-ytrue.flatten()))

def loss_mape(ytrue, pred):
    "MAPE"
    assert ytrue.shape == pred.shape
    y = ytrue.flatten()
    pred = pred.flatten()[y > 0]
    y = y[y>0]
    
    return np.mean(np.abs((pred-y) / y))

def loss_rmsle(ytrue, pred):
    "RMSLE"
    assert ytrue.shape == pred.shape
    return np.sqrt(mean_squared_error( np.log(1 + ytrue).flatten(), np.log(1 + pred).flatten() ))



In [4]:
import sys
import json
from models import ZmodelSEIRD, ZmodelPG, ZmodelBaseline

with open(DATA_PATH + 'backtesting/bt_seird_params.json', "r") as read_file:
    seird_params = json.load(read_file)
with open(DATA_PATH + 'backtesting/bt_pg_params.json', "r") as read_file:
    pg_params = json.load(read_file)



In [5]:
from datetime import timedelta

def single_back_eval_seird(df, reporting_date, params):
    
    preds_all = []
    for key, df_real in df.groupby('key'):
    
        df_short = df_real[df_real['date'] <= reporting_date]

        VAL_LEN = df['days'].max() - df_short['days'].max()
        if (VAL_LEN < 1) or (reporting_date.strftime("%Y-%m-%d") not in params):
            return None

        par = list(params[reporting_date.strftime("%Y-%m-%d")]['SEIRD'][key].values())
        preds = ZmodelSEIRD().predict(df_short, par, VAL_LEN)
        preds = preds[preds['t'] >= len(df_real)-VAL_LEN]

        preds['key'] = key
        preds['prediction_horizon'] = np.arange(len(preds)) + 1
        preds['days'] = preds['prediction_horizon'] + df_short['days'].max()
        preds['reporting_date'] = reporting_date
        preds['date'] = preds['reporting_date'] + pd.to_timedelta(preds['prediction_horizon'], unit='days')
        preds['date_eow'] = preds['date'] - pd.to_timedelta(preds['date'].dt.weekday, unit='days') + datetime.timedelta(days=6)

        real = preds[['key', 'date']].merge(df[['key', 'date', 'confirmed', 'recovered', 'deaths']],
                                            how='left', on=['key', 'date'])
        real = real.melt(id_vars = ['key', 'date'], value_vars = ['confirmed', 'recovered', 'deaths'],
                         value_name='realized', var_name='target')

        preds = preds.melt(id_vars = ['key', 'reporting_date', 'prediction_horizon', 'days', 'date', 'date_eow'],
                   value_vars = ['confirmed', 'recovered', 'deaths'], value_name='predicted', var_name='target')

        preds = preds.merge(real, how='left', on=['key', 'date', 'target'])
        preds['model'] = 'SEIRD'
        
        preds_all.append(preds)
    
    return pd.concat(preds_all)

def single_back_eval_pg(df, reporting_date, params):
    
    preds = []
    for key, df_real in df.groupby('key'):
        
        df_short = df_real[df_real['date'] <= reporting_date]

        VAL_LEN = df['days'].max() - df_short['days'].max()
        if (VAL_LEN < 1) or (reporting_date.strftime("%Y-%m-%d") not in params):
            return None

        for tgt in ['confirmed', 'deaths', 'recovered']:
            model = ZmodelPG()
            model.params = params[reporting_date.strftime("%Y-%m-%d")]['PG model'][tgt]

            preds_delta = model.predict(df_short[tgt].values.reshape(1,-1), VAL_LEN)
            preds_delta = pd.DataFrame({
                            'key':key,
                            'reporting_date':reporting_date,
                            'model':'PG',
                            'date':df_real['date'].values,
                            'days':df_real['days'].values,
                            'target':tgt,
                            'realized':df_real[tgt].values,
                            'predicted':preds_delta.reshape(-1)})
            preds_delta = preds_delta[preds_delta['date'] > preds_delta['reporting_date']]
            preds_delta['prediction_horizon'] = np.arange(1, VAL_LEN+1)
            preds_delta['date_eow'] = preds_delta['date'] - \
                    pd.to_timedelta(preds_delta['date'].dt.weekday, unit='days') + datetime.timedelta(days=6)
            preds.append(preds_delta)

    return pd.concat(preds)


def single_back_eval_baseline(df, reporting_date, params):
    
    preds = []
    for key, df_real in df.groupby('key'):
        
        df_short = df_real[df_real['date'] <= reporting_date]

        VAL_LEN = df['days'].max() - df_short['days'].max()
        if (VAL_LEN < 1):
            return None

        for tgt in ['confirmed', 'deaths', 'recovered']:
            model = ZmodelBaseline()

            preds_delta = model.predict(df_short[tgt].values.reshape(1,-1), VAL_LEN)
            preds_delta = pd.DataFrame({
                            'key':key,
                            'reporting_date':reporting_date,
                            'model':'Baseline',
                            'date':df_real['date'].values,
                            'days':df_real['days'].values,
                            'target':tgt,
                            'realized':df_real[tgt].values,
                            'predicted':preds_delta.reshape(-1)})
            preds_delta = preds_delta[preds_delta['date'] > preds_delta['reporting_date']]
            preds_delta['prediction_horizon'] = np.arange(1, VAL_LEN+1)
            preds_delta['date_eow'] = preds_delta['date'] - \
                    pd.to_timedelta(preds_delta['date'].dt.weekday, unit='days') + datetime.timedelta(days=6)
            preds.append(preds_delta)

    return pd.concat(preds)


def single_back_eval(df, dt, params, model):
    if model == 'SEIRD':
        return single_back_eval_seird(df, dt, params)
    elif model == 'PG':
        return single_back_eval_pg(df, dt, params)
    elif model == 'Baseline':
        return single_back_eval_baseline(df, dt, params)
    else:
        return None


In [6]:
from datetime import timedelta
from joblib import Parallel, delayed
import multiprocessing
import time
from tqdm import tqdm

start_time = time.time()

res = Parallel(n_jobs=8, temp_folder="/tmp", max_nbytes=None, backend="multiprocessing")\
    (delayed(single_back_eval)\
        (df, reporting_date, params, model)
            for reporting_date in [df['date'].min() + timedelta(days=30+i) for i in range(df['days'].max())] \
            #for reporting_date in tqdm([df['date'].min() + timedelta(days=30+i) for i in range(df['days'].max())]) \
            for model, params in [('SEIRD', seird_params), ('PG', pg_params), ('Baseline', None)]
    )

res_df = pd.concat([x for x in res if x is not None])
print(res_df.shape)
print(f"Finished in {time.time() - start_time:6.2f}s")


(17084331, 10)
Finished in 591.90s


In [7]:

def gen_agg_losses(df, loss_f_list, horizons=[7,14,21,28], min_cases=[0,100], date_col='reporting_date'):
    res = []
    for mc in min_cases:
        for hor in horizons:
            for loss_f in loss_f_list:
                df2 = df[(df['prediction_horizon'] == hor) & (df['realized'] >= mc)]
                l = df2.groupby(['model', date_col, 'target']).\
                    apply(lambda z: loss_f(z['realized'].values, z['predicted'].values)).rename("loss").reset_index()
                l['loss_func'] = loss_f.__doc__
                l['prediction_horizon'] = hor
                l['min_cases'] = mc
                res.append(l)
    return pd.concat(res)
    
#agg_losses = gen_agg_losses(res_df, [loss_rmsle, loss_mape], date_col='reporting_date')
agg_losses = gen_agg_losses(res_df[res_df['key'] != 'Tajikistan'], [loss_rmsle, loss_mape], date_col='reporting_date')

global_confirmed = df.groupby('date')['confirmed_new'].sum()
global_confirmed = global_confirmed[global_confirmed.index >= agg_losses['reporting_date'].min()]

agg_losses.head()



model reporting_date     target      loss loss_func  prediction_horizon  \
0  Baseline     2020-02-21  confirmed  0.648406     RMSLE                   7   
1  Baseline     2020-02-21     deaths  0.241740     RMSLE                   7   
2  Baseline     2020-02-21  recovered  0.439138     RMSLE                   7   
3  Baseline     2020-02-22  confirmed  0.732242     RMSLE                   7   
4  Baseline     2020-02-22     deaths  0.248367     RMSLE                   7   

   min_cases  
0          0  
1          0  
2          0  
3          0  
4          0

In [11]:
import plotly.io as pio

# change horizon here
HORIZON = 28

data = [dict(
  type = 'scatter',
  #x = agg_losses['reporting_date'],
  x = agg_losses['reporting_date'],
  y = agg_losses['loss'].round(4),
  name = z,
  yaxis='y1',
  line = dict(dash='dash') if z == 'Baseline' else dict(dash='solid'),
  transforms = [
      dict(type = 'filter', target = agg_losses['loss_func'], orientation = '=', value = agg_losses['loss_func'].unique()[0]),
      dict(type = 'filter', target = agg_losses['target'], orientation = '=', value = agg_losses['target'].unique()[0]),
      dict(type = 'filter', target = agg_losses['prediction_horizon'], orientation = '=', value = HORIZON),
      dict(type = 'filter', target = agg_losses['min_cases'], orientation = '=', value = 100),
      dict(type = 'filter', target = agg_losses['model'], orientation = '=', value = z),
  ]) for z in agg_losses['model'].unique()] + \
  [dict(
  type = 'bar',
  x = global_confirmed.index,
  y = global_confirmed.values,
  marker=dict(color="gray", opacity=0.2),
  yaxis='y2',
  name = 'Global daily<br>new cases',
  transforms = [ # dummy
      dict(type = 'filter', target = 'dummystring', orientation = '!=', value = ''),
      dict(type = 'filter', target = 'dummystring', orientation = '!=', value = ''),
      dict(type = 'filter', target = 'dummystring', orientation = '!=', value = ''),
      dict(type = 'filter', target = 'dummystring', orientation = '!=', value = ''),
      ]
  ),
  ]

layout = dict(
    xaxis=dict(title='Forecast date'),
    yaxis=dict(title="RMSLE"),
    yaxis2=dict(overlaying='y', side='right', showticklabels=True, showgrid=False, title='new confirmed cases'),
    width=1800,
    height=900,
    font=dict(family='Arial', size=24, color="black"),
    legend=dict(
        x=0.80,
        y=1,
        traceorder="normal",
        font=dict(
            family="sans-serif",
            size=24,
            color="black"
        ),
        bordercolor="Black",
        borderwidth=2
    ),
    margin=dict(l=90, r=110, t=0, b=80),
)

fig = {'data':data, 'layout':layout}


pio.show({'data':data, 'layout':layout}, validate=False)
pio.write_image(fig, f"{SAVE_PATH}/error_time_min100_{HORIZON}days.png", validate=False)



In [9]:

def gen_agg_losses2(df, loss_f_list, horizons=[7,14,21,28], date_col='reporting_date'):
    df0 = df.merge(df[(df['prediction_horizon']==1) & (df['model'] == 'Baseline')]\
             [['key', 'target', 'date', 'realized']].\
             rename({'realized':'forecast_realized', 'date':'reporting_date'}, axis=1), \
             how='left', on=['key', 'target', 'reporting_date'])
    df0 = df0[~df0['forecast_realized'].isnull()]
    res = []
    for hor in horizons:
        for loss_f in loss_f_list:
            df2 = df0[df0['prediction_horizon'] == hor]
            l = df2.groupby([df2['model'], 
                    (2**np.floor(np.log2(df2['forecast_realized']))).astype(int).rename('bucket'),
                    df2['target']]).\
                    apply(lambda z: pd.Series({'loss': loss_f(z['realized'].values, z['predicted'].values), 'n':len(z)})).\
                    reset_index()
            l['loss_func'] = loss_f.__doc__
            l['prediction_horizon'] = hor
            res.append(l)
    return pd.concat(res)
    
#agg_losses2 = gen_agg_losses2(res_df, [loss_rmsle, loss_mape], date_col='reporting_date')
agg_losses2 = gen_agg_losses2(res_df[res_df['key'] != 'Tajikistan'], [loss_rmsle, loss_mape], date_col='reporting_date')

agg_losses2.head()


model  bucket     target      loss        n loss_func  \
0  Baseline       0  confirmed  0.986254   3541.0     RMSLE   
1  Baseline       0     deaths  0.408206  10408.0     RMSLE   
2  Baseline       0  recovered  0.789362   7030.0     RMSLE   
3  Baseline       1  confirmed  1.321302    887.0     RMSLE   
4  Baseline       1     deaths  0.529474   2421.0     RMSLE   

   prediction_horizon  
0                   7  
1                   7  
2                   7  
3                   7  
4                   7

In [10]:
def human_format(num):
    if num < 2:
        return str(num)
    magnitude = 0
    while abs(num) >= 1000:
        magnitude += 1
        num /= 1000.0
    # add more suffixes if you need them
    return '%d%s+' % (num, ['', 'K', 'M', 'G', 'T', 'P'][magnitude])

agg_losses2['bucket2'] = agg_losses2['bucket'].apply(human_format)
agg_losses2['bucket2_shift'] = agg_losses2.groupby("target").shift(-1)['bucket2'].fillna("")
agg_losses2.loc[agg_losses2.bucket2_shift == 0, 'bucket2_shift'] = ""
agg_losses2['bucket3'] = agg_losses2.apply(lambda x: str(x["bucket2"]) + " - " + str(x["bucket2_shift"]) if x["bucket2_shift"] != "" else x["bucket2"], axis=1)
agg_losses2.loc[agg_losses2['bucket3'].str.endswith(" - 0"), 'bucket3'] = agg_losses2.loc[agg_losses2['bucket3'].str.endswith(" - 0"), 'bucket3'].str.replace(" - 0", "+")

# change horizon here
HORIZON = 28

data = [dict(
  type = 'lines',
  x = agg_losses2['bucket3'],
  y = agg_losses2['loss'].round(4),
  name = z,
  #yaxis='y1',
  line = dict(dash='dash') if z == 'Baseline' else dict(dash='solid'),
  transforms = [
      dict(type = 'filter', target = agg_losses2['loss_func'], orientation = '=', value = agg_losses2['loss_func'].unique()[0]),
      dict(type = 'filter', target = agg_losses2['target'], orientation = '=', value = agg_losses2['target'].unique()[0]),
      dict(type = 'filter', target = agg_losses2['prediction_horizon'], orientation = '=', value = HORIZON),
      dict(type = 'filter', target = agg_losses2['model'], orientation = '=', value = z),
  ]) for z in agg_losses2['model'].unique()] + \
  [dict(
  type = 'bar',
  x = agg_losses2['bucket3'],
  y = agg_losses2['n'],
  marker=dict(color="gray", opacity=0.1),
  yaxis='y2',
  name = '# observations',
  transforms = [ # dummy
      dict(type = 'filter', target = agg_losses2['loss_func'], orientation = '=', value = agg_losses2['loss_func'].unique()[0]),
      dict(type = 'filter', target = agg_losses2['target'], orientation = '=', value = agg_losses2['target'].unique()[0]),
      dict(type = 'filter', target = agg_losses2['prediction_horizon'], orientation = '=', value = HORIZON),
      dict(type = 'filter', target = agg_losses2['model'], orientation = '=', value = agg_losses2['model'].unique()[0]),
      ]
  ),
  ]

layout = dict(
    yaxis=dict(title='RMSLE'),
    xaxis=dict(title='Number of cases', tickangle=315),
    yaxis2=dict(overlaying='y', side='right', showticklabels=True, showgrid=False, title="nr. of observations"),
    width=1800,
    height=900,
    font=dict(family='Arial', size=24, color="black"),
    legend=dict(
        x=0.85,
        y=0.95,
        traceorder="normal",
        font=dict(
            family="sans-serif",
            size=24,
            color="black"
        ),
        bordercolor="Black",
        borderwidth=2
    ),
    margin=dict(l=90, r=110, t=0, b=150),
 )

fig = {'data':data, 'layout':layout}

pio.show({'data':data, 'layout':layout}, validate=False)
pio.write_image(fig, f"{SAVE_PATH}/error_numcases_{HORIZON}days.png", validate=False)

